In [1]:
import joblib
import weaviate
from weaviate.classes.query import (
    Filter, 
    Rerank
)

In [ ]:
import os

os.environ["COLLECTIONS_PATH"] = "./.collections"

In [3]:
import flask_app
import weaviate_server
from utils import (
    generate_with_single_input,
    print_object_properties,
    display_widget
)
#import unittests

2025-09-28 03:16:43.247673: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-09-28 03:16:43.571409: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX_VNNI AVX_VNNI_INT8 AVX_NE_CONVERT FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-09-28 03:16:44.869448: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.


 * Serving Flask app 'flask_app'
 * Debug mode: off


In [4]:
client = weaviate.connect_to_local(port=8079, grpc_port=50050)

In [5]:
print("Collections:", list(client.collections.list_all().keys()))

Collections: ['Bbc_collection']


In [6]:
bbc_data = joblib.load('data/bbc_data.joblib')

In [7]:
print_object_properties(bbc_data[0])

article_content: Justin Welby speaks on BBC Radio 4's Today programme as part of a special show guest edited by Dame ...(truncated)
description: The Archbishop of Canterbury urges politicians to "forswear wedge issues" and avoid divisive topics.
guid: https://www.bbc.co.uk/news/uk-67844356
link: https://www.bbc.co.uk/news/uk-67844356?at_medium=RSS&at_campaign=KARANGA
pubDate: 2024-01-01 00:00:04
title: Justin Welby: Political leaders should treat opponents as human beings



In [8]:
collection = client.collections.get("bbc_collection")

In [ ]:
# individual insert
#collection.data.insert(properties=bbc_data[0])

# batch insert
#with collection.batch.dynamic() as batch:
#    for item_data in bbc_data:
#        batch.add_object(item_data)

/opt/conda/lib/python3.11/site-packages/weaviate/warnings.py:256: UserWarning: Con002: You are using the datetime object 2024-01-01 00:00:04 without a timezone. The timezone will be set to UTC.
            To use a different timezone, specify it in the datetime object. For example:
            datetime.datetime(2021, 1, 1, 0, 0, 0, tzinfo=datetime.timezone(-datetime.timedelta(hours=2))).isoformat() = 2021-01-01T00:00:00-02:00
            
  warnings.warn(
/opt/conda/lib/python3.11/site-packages/weaviate/warnings.py:256: UserWarning: Con002: You are using the datetime object 2024-01-01 00:09:56 without a timezone. The timezone will be set to UTC.
            To use a different timezone, specify it in the datetime object. For example:
            datetime.datetime(2021, 1, 1, 0, 0, 0, tzinfo=datetime.timezone(-datetime.timedelta(hours=2))).isoformat() = 2021-01-01T00:00:00-02:00
            
  warnings.warn(
/opt/conda/lib/python3.11/site-packages/weaviate/warnings.py:256: UserWarning: C

In [9]:
print(f"The number of elements in the collection is: {len(collection)}")

The number of elements in the collection is: 9974


In [10]:
object = collection.query.fetch_objects(limit = 5, include_vector = True).objects[0]
print("Printing the properties (some will be truncated due to size)")
print_object_properties(object.properties)
print("Vector: (truncated)",object.vector['main_vector'][0:15])
print("Vector length: ", len(object.vector['main_vector']))

Printing the properties (some will be truncated due to size)
article_content: There are fewer than 100 available spaces left across the male prison estate in England and Wales, t...(truncated)
description: The government hopes that overcrowding will ease once new measures are brought in this September.
guid: https://www.bbc.com/news/articles/c0rw48nj282o#3
link: https://www.bbc.com/news/articles/c0rw48nj282o
pubDate: 2024-08-27 18:00:13+00:00
title: Under 100 spaces in men's prisons in England and Wales



KeyError: 'main_vector'

In [11]:

def filter_by_metadata(metadata_property: str, 
                       values: list[str], 
                       collection: "weaviate.collections.collection.sync.Collection" , 
                       limit: int = 5) -> list:
    """
    Retrieves objects from a specified collection based on metadata filtering criteria.

    This function queries a collection within the specified client to fetch objects that match 
    certain metadata criteria. It uses a filter to find objects whose specified 'property' contains 
    any of the given 'values'. The number of objects retrieved is limited by the 'limit' parameter.

    Args:
    metadata_property (str): The name of the metadata property to filter on.
    values (List[str]): A list of values to be matched against the specified property.
    collection_name (weaviate.collections.collection.sync.Collection): The collection to query.
    limit (int, optional): The maximum number of objects to retrieve. Defaults to 5.

    Returns:
    List[Object]: A list of objects from the collection that match the filtering criteria.
    """
    ### START CODE HERE ###
    
    # Retrieve using collection.query.fetch_objects
    response = collection.query.fetch_objects(limit = limit, include_vector = True, filters = Filter.by_property(metadata_property).contains_any(values))

    ### END CODE HERE ###
    
    response_objects = [x.properties for x in response.objects]
    
    return response_objects

In [12]:
# Let's get an example
res = filter_by_metadata('title', ['Taylor Swift'], collection, limit = 2)
for x in res:
    print_object_properties(x)

article_content: The 2024 awards season kicked off in style at the Golden Globes - the first major red carpet event o...(truncated)
description: Stars including Margot Robbie and Taylor Swift arrived in a variety of eye-catching outfits.
guid: https://www.bbc.co.uk/news/entertainment-arts-67908727
link: https://www.bbc.co.uk/news/entertainment-arts-67908727?at_medium=RSS&at_campaign=KARANGA
pubDate: 2024-01-08 03:23:58+00:00
title: Margot Robbie, Taylor Swift and more on Golden Globes red carpet

article_content: TikTok has removed music by stars including Taylor Swift, The Weeknd and Olivia Rodrigo from videos ...(truncated)
description: It comes after a licensing rights row between the platform and the artists' record label, Universal.
guid: https://www.bbc.co.uk/news/technology-68166028
link: https://www.bbc.co.uk/news/technology-68166028?at_medium=RSS&at_campaign=KARANGA
pubDate: 2024-02-01 17:17:45+00:00
title: TikTok mutes users' videos as it pulls Taylor Swift and The Weeknd's m

In [13]:
# GRADED CELL 

import weaviate.classes as wvc

def semantic_search_retrieve(query: str,
                             collection: "weaviate.collections.collection.sync.Collection" , 
                             top_k: int = 5) -> list:
    """
    Performs a semantic search on a collection and retrieves the top relevant chunks.

    This function executes a semantic search query on a specified collection to find text chunks 
    that are most relevant to the input 'query'. The search retrieves a limited number of top 
    matching objects, as specified by 'top_k'. The function returns the 'chunk' property of 
    each of the top matching objects.

    Args:
    query (str): The search query used to find relevant text chunks.
    collection (weaviate.collections.collection.sync.Collection): The collection in which the semantic search is performed.
    top_k (int, optional): The number of top relevant objects to retrieve. Defaults to 5.

    Returns:
    List[str]: A list of text chunks that are most relevant to the given query.
    """
    ### START CODE HERE ###

    # Retrieve using collection.query.near_text
    response = collection.query.near_text(limit  = top_k, query = query, return_metadata=wvc.query.MetadataQuery(distance=True))

    ### END CODE HERE ###
    
    response_objects = [x.properties for x in response.objects]
    
    return response_objects

In [14]:
# Let's have an example!
print_object_properties(semantic_search_retrieve(query = 'Tell me about the last Taylor Swift show', collection = collection, top_k = 2))

WeaviateQueryError: Query call with protocol GRPC search failed with message explorer: get class: vectorize params: could not vectorize input for collection Bbc_collection with search-type nearText. Make sure a vectorizer module is configured for this collection.

In [28]:
# GRADED CELL 

def bm25_retrieve(query: str, 
                  collection: "weaviate.collections.collection.sync.Collection" , 
                  top_k: int = 5) -> list:
    """
    Performs a BM25 search on a collection and retrieves the top relevant chunks.

    This function executes a BM25-based search query on a specified collection to identify text 
    chunks that are most relevant to the provided 'query'. It retrieves a limited number of the 
    top matching objects, as specified by 'top_k', and returns the 'chunk' property of these objects.

    Args:
    query (str): The search query used to find relevant text chunks.
    collection (weaviate.collections.collection.sync.Collection): The collection in which the BM25 search is performed.
    top_k (int, optional): The number of top relevant objects to retrieve. Defaults to 5.

    Returns:
    List[str]: A list of text chunks that are most relevant to the given query.
    """
    
    ### START CODE HERE ###

    # Retrieve using collection.query.bm25
    response = collection.query.bm25(limit  = top_k, include_vector = True, query = query, return_metadata=wvc.query.MetadataQuery(distance=True))

    ### END CODE HERE ### 
    
    response_objects = [x.properties for x in response.objects]
    return response_objects 

In [29]:
print_object_properties(bm25_retrieve('Tell me about the last Taylor Swift show', collection, top_k = 2))

article_content: There was a very special guest at Taylor Swift's most recent London show - the singer's boyfriend Tr...(truncated)
description: Kelce joined Swift on stage as a dancer for I Can Do It With a Broken Heart. 
guid: https://www.bbc.com/news/articles/c2999rpn6e5o#6
link: https://www.bbc.com/news/articles/c2999rpn6e5o
pubDate: 2024-06-24 07:31:17+00:00
title: Kelce makes surprise appearance during Taylor Swift show

article_content: The Tortured Poets Department, released on Friday, features 31 songs For two female journalists in t...(truncated)
description: From exes who wasted our time, to comfort-eating after a breakup. We've all been there and so has Swift.
guid: https://www.bbc.co.uk/news/entertainment-arts-68856232#1
link: https://www.bbc.co.uk/news/entertainment-arts-68856232
pubDate: 2024-04-20 15:36:19+00:00
title: How Taylor Swift captured modern dating despair




In [30]:
# GRADED CELL 

def hybrid_retrieve(query: str, 
                    collection: "weaviate.collections.collection.sync.Collection" , 
                    alpha: float = 0.5,
                    top_k: int = 5
                   ) -> list:
    """
    Performs a hybrid search on a collection and retrieves the top relevant chunks.

    This function executes a hybrid search that combines semantic vector search and traditional 
    keyword-based search on a specified collection to find text chunks most relevant to the 
    input 'query'. The relevance of results is influenced by 'alpha', which balances the weight 
    between vector and keyword matches. It retrieves a limited number of top matching objects, 
    as specified by 'top_k', and returns the 'chunk' property of these objects.

    Args:
    query (str): The search query used to find relevant text chunks.
    collection (weaviate.collections.collection.sync.Collection): The collection in which the hybrid search is performed.
    alpha (float, optional): A weighting factor that balances the contribution of semantic 
    and keyword matches. Defaults to 0.5.
    top_k (int, optional): The number of top relevant objects to retrieve. Defaults to 5.

    Returns:
    List[str]: A list of text chunks that are most relevant to the given query.
    """
    ### START CODE HERE ### 

    # Retrieve using collection.query.hybrid
    response = collection.query.hybrid(limit  = top_k, include_vector = True, alpha = alpha, query = query, return_metadata=wvc.query.MetadataQuery(distance=True))

    ### END CODE HERE ###
    
    response_objects = [x.properties for x in response.objects]
    
    return response_objects 

In [31]:
print_object_properties(hybrid_retrieve('Tell me about the last Taylor Swift show', collection, top_k = 2))

WeaviateQueryError: Query call with protocol GRPC search failed with message VectorFromInput was called without vectorizer on class Bbc_collection for input Tell me about the last Taylor Swift show.

In [32]:
# GRADED CELL 

def semantic_search_with_reranking(query: str, 
                                   rerank_property: str,
                                   collection: "weaviate.collections.collection.sync.Collection" , 
                                   rerank_query: str = None,
                                   top_k: int = 5
                                   ) -> list:
    """
    Performs a semantic search and reranks the results based on a specified property.

    Args:
        query (str): The search query to perform the initial search.
        rerank_property (str): The property used for reranking the search results.
        collection (weaviate.collections.collection.sync.Collection): The collection to search within.
        rerank_query (str, optional): The query to use specifically for reranking. If not provided, 
                                      the original query is used for reranking.
        top_k (int, optional): The maximum number of top results to return. Defaults to 5.

    Returns:
        list: A list of properties from the reranked search results, where each item corresponds to 
              an object in the collection.
    """
    ### START CODE HERE ### 

    # Set the rerank_query to be the same as the query if rerank_query is not passed (don't change this line)
    if rerank_query is None: 
        rerank_query = query 
        
    # Define the reranker with rerank_query and rerank_property
    reranker = Rerank(query = rerank_query, prop = rerank_property)

    # Retrieve using collection.query.near_text with the appropriate parameters (do not forget the rerank!)
    response = collection.query.near_text(limit = top_k, rerank = reranker, query = query)

    ### END CODE HERE ###
    
    response_objects = [x.properties for x in response.objects]
    
    return response_objects 

In [33]:
# Set a query
query = 'Tell me about the conflicts in Latin America'
# Get the results from a search (in this case the hybrid search)
results = semantic_search_with_reranking(query, collection = collection, top_k = 2, rerank_property = 'chunk')

WeaviateQueryError: Query call with protocol GRPC search failed with message no such prop with name 'chunk' found in class 'Bbc_collection' in the schema. Check your schema files for which properties in this class are available.

In [ ]:
print_object_properties(results)

In [36]:
def generate_final_prompt(query: str, 
                          top_k: int, 
                          retrieve_function: callable,
                          rerank_query: str = None, 
                          rerank_property: str = None, 
                          use_rerank: bool = False, 
                          use_rag: bool = True) -> str:
    """
    Generates a final prompt by optionally retrieving and formatting relevant documents using retrieval-augmented generation (RAG).

    Args:
        query (str): The initial query to be used for document retrieval.
        top_k (int): The number of top documents to retrieve and use for generating the prompt.
        retrieve_function (callable): The function used to retrieve documents based on the query.
        rerank_query (str, optional): The query used specifically for reranking documents if reranking is enabled.
        rerank_property (str, optional): The property used for reranking. Required if 'use_rerank' is True.
        use_rerank (bool, optional): Flag to denote whether to use reranking in document retrieval. Defaults to False.
        use_rag (bool, optional): Flag to determine whether to use retrieval-augmented generation. Defaults to True.

    Returns:
        str: A constructed prompt that includes the original query and formatted retrieved documents if 'use_rag' is True.
             Otherwise, it returns the original query.
    """
    # If no rag, return the query
    if not use_rag:
        return query
    
    if use_rerank:
        if rerank_property is None:
            raise ValueError('rerank_property must be set if use_rerank = True')
        top_k_documents = retrieve_function(query=query, top_k=top_k, collection = collection, rerank_property = rerank_property, rerank_query = rerank_query)
    else:
        top_k_documents = retrieve_function(query=query, top_k=top_k, collection = collection)
    
    # Initialize an empty string to store the formatted data.
    formatted_data = ""
    
    # Iterate over each retrieved document.
    for document in top_k_documents:
        # Format each document into a structured string.
        document_layout = (
            f"Title: {document['title']}, Chunk: {document['chunk']}, "
            f"Published at: {document['pubDate']}\nURL: {document['link']}"
        )
        # Append the formatted string to the main data string with a newline for separation.
        formatted_data += document_layout + "\n"
    
    # If use_rag flag is True, construct the enhanced prompt with the augmented data.
    retrieve_data_formatted = formatted_data  # Store formatted data.
    prompt = (
        f"Answer the user query below. There will be provided additional information for you to compose your answer. "
        f"The relevant information provided is from 2024 and it should be added as your overall knowledge to answer the query, "
        f"you should not rely only on this information to answer the query, but add it to your overall knowledge."
        f"The news data is ordered by relevance."
        f"Query: {query}\n"
        f"2024 News: {retrieve_data_formatted}"
    )
    
    return prompt

In [37]:
prompt = generate_final_prompt("Tell me the economic situation of the US in 2024.", top_k = 5, retrieve_function = semantic_search_retrieve, use_rerank = False, rerank_property = 'title')

WeaviateQueryError: Query call with protocol GRPC search failed with message explorer: get class: vectorize params: could not vectorize input for collection Bbc_collection with search-type nearText. Make sure a vectorizer module is configured for this collection.

In [ ]:
print(prompt)

In [38]:
def llm_call(query: str, 
             retrieve_function: callable = None, 
             top_k: int = 5, 
             use_rag: bool = True, 
             use_rerank: bool = False, 
             rerank_property: str = None, 
             rerank_query: str = None) -> str:
    """
    Simulates a call to a language model by generating a prompt and using it to produce a response.

    Args:
        query (str): The initial query for which a response is sought.
        retrieve_function (callable, optional): The function used to retrieve documents related to the query.
        top_k (int, optional): The number of top documents to retrieve and use for generating the prompt. Defaults to 5.
        use_rag (bool, optional): Indicates whether to use retrieval-augmented generation. Defaults to True.
        use_rerank (bool, optional): Indicates whether to apply reranking to the retrieved documents. Defaults to False.
        rerank_property (str, optional): The property to use for reranking. Required if 'use_rerank' is True.
        rerank_query (str, optional): The query used specifically for reranking documents if reranking is enabled.

    Returns:
        str: The generated response content after processing the prompt with a language model.
    """
    
    # Get the prompt
    PROMPT = generate_final_prompt(query, top_k = top_k, retrieve_function = retrieve_function, use_rag = use_rag, use_rerank = use_rerank, rerank_property = rerank_property, rerank_query = rerank_query)
    
    generated_response = generate_with_single_input(PROMPT)

    generated_message = generated_response['content']
    
    return generated_message

In [39]:
query = "Tell me about United States and Brazil's relationship over the course of 2024. Provide links for the resources you use in the answer."

In [40]:
# Result with reranked results
print(llm_call(query = query, 
               top_k = 5, 
               retrieve_function = hybrid_retrieve, 
               ))

WeaviateQueryError: Query call with protocol GRPC search failed with message VectorFromInput was called without vectorizer on class Bbc_collection for input Tell me about United States and Brazil's relationship over the course of 2024. Provide links for the resources you use in the answer..